In [1]:
CODON_TABLE = {'AAA': 'K',
 'AAC': 'N', 'AAG': 'K', 'AAU': 'N', 'ACA': 'T',
 'ACC': 'T', 'ACG': 'T', 'ACU': 'T','AGA': 'R',
 'AGC': 'S', 'AGG': 'R', 'AGU': 'S', 'AUA': 'I',
 'AUC': 'I', 'AUG': 'M', 'AUU': 'I', 'CAA': 'Q',
 'CAC': 'H', 'CAG': 'Q', 'CAU': 'H', 'CCA': 'P',
 'CCC': 'P', 'CCG': 'P', 'CCU': 'P', 'CGA': 'R',
 'CGC': 'R', 'CGG': 'R', 'CGU': 'R', 'CUA': 'L',
 'CUC': 'L', 'CUG': 'L', 'CUU': 'L', 'GAA': 'E',
 'GAC': 'D', 'GAG': 'E', 'GAU': 'D', 'GCA': 'A',
 'GCC': 'A', 'GCG': 'A', 'GCU': 'A', 'GGA': 'G',
 'GGC': 'G', 'GGG': 'G', 'GGU': 'G', 'GUA': 'V',
 'GUC': 'V', 'GUG': 'V', 'GUU': 'V', 'UAA': '*',
 'UAC': 'Y', 'UAG': '*', 'UAU': 'Y', 'UCA': 'S',
 'UCC': 'S', 'UCG': 'S', 'UCU': 'S', 'UGA': '*',
 'UGC': 'C', 'UGG': 'W', 'UGU': 'C', 'UUA': 'L',
 'UUC': 'F', 'UUG': 'L', 'UUU': 'F'}

**Генераторы. Базовый уровень**

Что будет, если мы попытаемся сделать кортеж по аналогии со списком? (просто поменяв скобочки)

In [265]:
tuple_question = (x ** 2 for x in range(10))
print (tuple_question, type(tuple_question))

<generator object <genexpr> at 0x10f139620> <class 'generator'>


Какой-то неправильный кортеж

In [267]:
tuple_question[0]

TypeError: 'generator' object is not subscriptable

![generator](i-am-a-generator.jpg)

Объект, который мы получили называется генератор. В чем отличие его от списка/кортежа ? 

По нему точно так же можно итерироваться 

In [270]:
squares = (x ** 2 for x in range(5))
for s in squares:
    print (s)

0
1
4
9
16


Один раз

In [271]:
for s in squares:
    print (s)

Генератор - один из способов реализации концепции ленивых вычислений. Мы пишем, что за вычисления нужно осуществить, а осуществлены они будут только тогда, когда это непосредственно потребуется.
Таким образом в памяти будет храниться лишь минимум информации, необходимой для осуществления этого вычисления.

In [310]:
%%timeit
squares = [x ** 2 for x in range(100000)]
for s in squares:
    if s % 99000000000 == 0:
        pass

33.2 ms ± 1.48 ms per loop (mean ± std. dev. of 7 runs, 10 loops each)


In [311]:
%%timeit
squares_generator = (x ** 2 for x in range(100000))
for s in squares_generator:
    if s % 99000000000 == 0:
        pass

37.7 ms ± 524 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)


По скорости нет разности. Даже в случае с генератором чуть медленнее (это лишь пока мы не уперлись в лимит по памяти)

Для использования memory_profiler надо выполнить следующие команды

conda install -c chroxvi memory_profiler

conda install -c anaconda psutil

In [5]:
%load_ext memory_profiler

In [161]:
%%memit
squares = [x ** 2 for x in range(10000000)]
for s in squares:
    if s % 99000000000 == 0:
        print (s)
    


0
10890000000000
43560000000000
98010000000000
peak memory: 483.82 MiB, increment: 383.14 MiB


In [30]:
del squares

In [6]:
%%memit
squares_generator = (x ** 2 for x in range(10000000))
for s in squares_generator:
    if s % 99000000000 == 0:
        print (s)

0
10890000000000
43560000000000
98010000000000
peak memory: 47.03 MiB, increment: 0.16 MiB


Видим, что использование памяти в случае с генератором минимально, в случае списка мы же получаем огромный оверхэд по памяти.

Когда нам уже случалось использовать генератор? На самом деле при чтении файла с помощью конструкции for line in file мы используем именно генератор - файл не подгружается полностью, а частями, такими, чтобы минимизировать использование памяти, но при этом не замедлить исполняемый код

Для использования кода ниже, если у вас Windows просто загрузите файл по [ссылке](https://www.genome.wisc.edu/pub/sequence/U00096.2.fas)

In [162]:
!wget https://www.genome.wisc.edu/pub/sequence/U00096.2.fas

--2020-03-17 12:55:35--  https://www.genome.wisc.edu/pub/sequence/U00096.2.fas
Resolving www.genome.wisc.edu (www.genome.wisc.edu)... 128.104.81.186
Connecting to www.genome.wisc.edu (www.genome.wisc.edu)|128.104.81.186|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4697740 (4.5M) [text/plain]
Saving to: ‘U00096.2.fas.1’

U00096.2.fas.1      100%[===================>]   4.48M  2.56MB/s    in 1.7s    

2020-03-17 12:55:38 (2.56 MB/s) - ‘U00096.2.fas.1’ saved [4697740/4697740]



In [8]:
path_to_fasta_file = "U00096.2.fas"

In [164]:
from collections import Counter

In [165]:
cnt = Counter()

In [166]:
%%memit
def process_line(line, cnt):
    cnt.update(line)

global_cnt = Counter()
with open(path_to_fasta_file) as in_file:
    in_file.readline()
    for line in in_file:
        process_line(line, global_cnt)
print (global_cnt.most_common())

[('c', 1179554), ('g', 1176923), ('a', 1142228), ('t', 1140970), ('\n', 57996)]
peak memory: 483.86 MiB, increment: 0.00 MiB


In [48]:
del in_file
del global_cnt

Сравним просто с зачитыванием всего файла в память

In [53]:
%%memit
def process_line(line, cnt):
    cnt.update(line)

global_cnt = Counter()
with open(path_to_fasta_file) as in_file:
    in_file.readline()
    lines = in_file.readlines()
    for line in lines:
        process_line(line, global_cnt)
print (global_cnt.most_common())

[('c', 1179554), ('g', 1176923), ('a', 1142228), ('t', 1140970), ('\n', 57996)]
peak memory: 61.47 MiB, increment: 0.00 MiB


In [54]:
del in_file
del global_cnt

Генераторы можно использовать при создании других генераторов. При этом ни на одном из этапов мы не разворачиваем в памяти весь требуемый список, потому использование памяти минимально

In [167]:
%%memit
squares = (x ** 2 for x in range(1000))
squares_with_1_on_2 = (x for x in squares if (x % 100) // 10 == 1)
squares_with_1_on_2_div7 = (x for x in squares_with_1_on_2 if x % 7 == 0)
squares_with_1_on_2_div7_add3 = map(lambda x : x + 3, squares_with_1_on_2_div7)

sm = sum(squares_with_1_on_2_div7_add3)

peak memory: 483.86 MiB, increment: 0.00 MiB


Генераторы - одно из мощнейших средств Python. Они позволяют, единожды написав какие-то обработчики данных, 
дальше использовать их, соединять друг с другом и тд без дополнительных затрат по памяти.

Более близкий пример - посчитать число разных кодонов в нуклеотидной последовательности, кодирующей белок

In [77]:
start_codon = 'AUG'
stop_codons = ['UAA','UAG', 'UGA']
coding_codons = list(set(CODON_TABLE) - set(stop_codons))
seq = start_codon +  "".join(random.choice(coding_codons) for _ in range(1000)) + random.choice(stop_codons)

In [78]:
codons = (seq[i:i+3] for i in range(0, len(seq), 3))
aminoacids = (CODON_TABLE[c] for c in codons)
cnt = Counter(aminoacids)
print (cnt.most_common())

[('L', 100), ('R', 97), ('S', 93), ('V', 67), ('T', 67), ('G', 67), ('P', 65), ('A', 56), ('I', 55), ('D', 38), ('Y', 36), ('N', 34), ('K', 33), ('E', 33), ('H', 33), ('Q', 32), ('C', 31), ('F', 29), ('M', 19), ('W', 16), ('*', 1)]


Для работы с итерируемыми объектами, частности, с генераторами, существует множество встроенных функций

**enumerate** - принимает итератор и возвращает итератор, который возвращает кортежи из (индекс, элемент_исходного итератора)

In [ ]:
?enumerate

In [84]:
aminoacids = CODON_TABLE.values()

print (next(enumerate(aminoacids)))

for ind, ac in enumerate(aminoacids):
    print (ind, ac)
    if ind == 4:
        break


(0, 'K')
0 K
1 N
2 K
3 N
4 T


Можно задать начало отчета (удобно, когда хочется иметь нумерацию с 1, например)

In [85]:
start = 1
for ind, ac in enumerate(aminoacids, start):
    print (ind, ac)
    if ind == 4:
        break

1 K
2 N
3 K
4 N


In [86]:
?zip

**zip** - принимает итераторы, возвращает кортежи, где i элемент кортежа происходит из i итератора. 

In [89]:
for t in zip(range(3), range(3, 6)):
    print (t)
    
for i, j in zip(range(3, 6), range(6, 9)):
    print (i, j)    

(0, 3)
(1, 4)
(2, 5)
3 6
4 7
5 8


С ним надо быть аккуратным. Если какой-то итератор содержит больше значений, чем другие, то эти значения просто не покажутся

In [90]:
for i, j in zip(range(3, 6), range(6, 20)):
    print (i, j)   

3 6
4 7
5 8


**reversed** - возвращает итератор, идущий в обратную сторону по контейнеру (как и следует из названия). Полезен, например, тем, что обычно использующийся для списков способ создает новый список, а этот - нет

In [111]:
lst = [random.choice("ATGC") for i in range(10000000)]

In [112]:
%%memit
for i in lst[::-1]:
    if i == "G":
        break

peak memory: 213.62 MiB, increment: 76.30 MiB


In [113]:
%%memit
for i in reversed(lst):
    if i == "G":
        break

peak memory: 213.62 MiB, increment: 0.00 MiB


Пример использования

In [114]:
def rindex(lst, query):
    for ind, val in enumerate(reversed(lst)):
        if val == query:
            return len(lst) - ind - 1
    return -1

In [117]:
rindex([1,2,3,10,15,4], 3)

2

**Itertools**

Много функций для работы с итераторами содержатся и в стандартном пакете

In [170]:
from itertools import count, cycle, repeat, chain, compress, dropwhile, takewhile, islice

**count** - бесконечный счетчик

In [130]:
cnt = count(5)
for _ in range(7):
    print (next(cnt))

5
6
7
8
9
10
11


**cycle** - бесконечный циклический итератор

In [131]:
frames = (0, 1, 2)
cycle_frames = cycle(frames)
for _ in range(7):
    print (next(cycle_frames))

0
1
2
0
1
2
0


**repeat** - просто итератор, который бесконечно возвращает одно и то же значение

Документация говорит, что полезно использовать, например, как источник константных значений для zip

In [132]:
list(map(pow, range(10), repeat(2)))

[0, 1, 4, 9, 16, 25, 36, 49, 64, 81]

**chain** - принимает несколько итераторов и объединяет их в один

In [135]:
for i in chain(range(5,7), range(17, 19)):
    print (i)

5
6
17
18


**chain.from_iterable** - делает то же самое, но принимает один итератор, который возвращает другие итераторы

In [137]:
for i in chain.from_iterable(range(1, x) for x in range(3, 6)):
    print (i)

1
2
1
2
3
1
2
3
4


**compress** - принимает на вход итератор со значениями и итератор с булевыми переменными, обозначающими брать нужную переменную или нет

In [139]:
for i in compress("ATGC", [True, False, True, False]):
    print (i)

A
G


**dropwhile** - не берет значения из итератора, пока выполняется условие, после этого возвращает остаток

In [174]:
list(dropwhile(lambda y : y < 255000, 
               (sum(i** 2 for i in range(0, x)) for x in range(5, 100))))

[255346, 263810, 272459, 281295, 290320, 299536, 308945, 318549]

**takewhile** - наоборот, берет значения пока выполняется условие

In [159]:
list(takewhile(lambda y : y < 150, (sum(i** 2 for i in range(0, x)) for x in range(5, 100)) ))

[30, 55, 91, 140]

**islice** - взять срез по итератору

In [291]:
a = (x ** 2 for x in range(10))
print (list(islice(a, 0, 3)))
print (list(islice(a, 0, 3)))

[0, 1, 4]
[9, 16, 25]


In [177]:
a = (x ** 2 for x in range(10))
d = islice(a, 0, 3)
e = islice(a, 0, 3)
print(list(e))
print(list(d))

[0, 1, 4]
[9, 16, 25]


Отдельно стоят итераторы, позволяющие делать всякие комбинаторные вещи

In [161]:
from itertools import product, combinations, permutations, combinations_with_replacement

**product** - декартово произведение

In [165]:
list(product(range(3), range(3))) 

[(0, 0), (0, 1), (0, 2), (1, 0), (1, 1), (1, 2), (2, 0), (2, 1), (2, 2)]

**combinations**

In [168]:
list(combinations("ATGC", 2))

[('A', 'T'), ('A', 'G'), ('A', 'C'), ('T', 'G'), ('T', 'C'), ('G', 'C')]

и т.д:)

**Многострочные генераторы**

До данного момента мы с вами писали только однострочные генераторы. Одна часто хочется написать какую-то сложную функцию, которая работает по тому же принципу, тратя мало памяти на вычисления. Для этого существует специальный синтаксис - **yield**

Напишем, например, генератор чисел Фибоначчи

In [189]:
def get_counter(start):
    s = start - 1
    def counter():
        nonlocal s
        s +=1 
        return s
    return counter

In [194]:
def get_counter(start):
    i= start
    while True:
        yield i
        i += 1


In [184]:
def fibonacci_gen():
    print("HI")
    f0, f1 = 0, 1
    while True: 
        yield f0 #!
        f0, f1 = f1, f0 + f1

In [196]:
cnt = get_counter(4)

In [185]:
fibonacci_gen()

<generator object fibonacci_gen at 0x1072468b8>

In [186]:
fib_gen = fibonacci_gen()
for i in range(5):
    print(next(fib_gen))

HI
0
1
1
2
3


In [ ]:
#for i in fib_gen:
#    print(i)

In [174]:
fib_gen = fibonacci_gen()
list(takewhile(lambda x : x < 100, fib_gen))

[0, 1, 1, 2, 3, 5, 8, 13, 21, 34, 55, 89]

После выполнения команды **yield**, функция возвращает значение f0, но она завершается, а только замирает. Следующий вызов к ней "пробуждает функцию", она делает еще одну итерацию бесконечного цикла и снова замирает, возвращая значение


Можем написать функцию, которая вернет нам итераторы по всем белкам на данной цепи (будем считать, что белки не могут быть вложенными)

In [2]:
def transcribe(n, tr_table={"A" : "A", "T" : "U", "G" : "G", "C" : "C"}):
    return tr_table[n]

def iter_seqs(in_file_path):
    open_frames = cycle([0,1,2])
    proteins = [None, None, None]
    with open(path_to_fasta_file) as in_file:
        in_file.readline()
        letters = chain.from_iterable((line for line in in_file))
        
        dna_nucleotides = filter(lambda x : x != "\n", letters)
        
        nucleotides = map(lambda x : transcribe(x.upper()), dna_nucleotides)
        
        triplet = "".join(islice(nucleotides, 0,3))
        
        nucleotides = chain(nucleotides, ('END',)) # чтобы не пропускать последний нуклеотид
        for n in nucleotides:
            open_frame = next(open_frames)
            cur_prot = proteins[open_frame]
            ac = CODON_TABLE[triplet]
            if ac == "*":
                if cur_prot:
                    proteins[open_frame] = None
                    cur_prot.append(triplet)
                    yield cur_prot
            elif ac == "M" and cur_prot is None:
                proteins[open_frame] = [triplet]
            elif cur_prot is not None:
                cur_prot.append(triplet)
            triplet = triplet[1:] + n
        

In [9]:
with open(path_to_fasta_file) as in_file:
    in_file.readline()
    print (in_file.readline())

agcttttcattctgactgcaacgggcaatatgtctctgtgtggattaaaaaaagagtgtctgatagcagcttctgaactg



In [15]:
from itertools import cycle, chain, islice

In [16]:
%%memit -i 0.1 -c -o
prots_gen = iter_seqs(path_to_fasta_file)
codon_usage_cnt = Counter()
for prot_codons in prots_gen:
    codon_usage_cnt.update(prot_codons)

peak memory: 85.41 MiB, increment: 6.48 MiB


<MemitResult : peak memory: 85.41 MiB, increment: 6.48 MiB>

In [17]:
print (codon_usage_cnt.most_common())

[('AUG', 76237), ('CUG', 53366), ('GCG', 46843), ('AAA', 44178), ('CAG', 43663), ('CGC', 40163), ('AUC', 39387), ('GAA', 39022), ('GCC', 38774), ('UUU', 37874), ('GGC', 36781), ('AUU', 36398), ('GAU', 35561), ('ACC', 33525), ('CCG', 33307), ('UUC', 33123), ('AAC', 32709), ('GCA', 32215), ('GUG', 31416), ('AAU', 30160), ('AGC', 29603), ('GGU', 29316), ('UUG', 28908), ('GUU', 28896), ('ACG', 28215), ('UGG', 28080), ('UGC', 26329), ('CGU', 26240), ('GCU', 25462), ('CCA', 24276), ('UUA', 24116), ('CAU', 23838), ('CGG', 23805), ('GUC', 23643), ('AAG', 23143), ('UCG', 23086), ('CAA', 22849), ('UCA', 22774), ('GAC', 22113), ('CAC', 21484), ('AUA', 21081), ('GUA', 19901), ('GAG', 19893), ('UAU', 19577), ('UCC', 18734), ('CUU', 18611), ('UGA', 18311), ('UAC', 17833), ('ACA', 17638), ('CUC', 17231), ('AGU', 16749), ('GGG', 16321), ('ACU', 15999), ('UCU', 15969), ('GGA', 15646), ('UAA', 15573), ('CCC', 15446), ('CGA', 15273), ('UGU', 15088), ('CCU', 14393), ('AGA', 14140), ('AGG', 13613), ('CUA',

Что дают генераторы:

![generators](generators_pipelines.png)

**Coroutines**

Начиная с Python2.5 появилась возможность не только получать значение из генератора, но и посылать их туда. Это плавно дает возможность использовать генератор как корутину - сопрограмму. То есть можно сделать набор функций, общающихся друг с другом и выдающим в конце результат результат. 

Общение происходит с помощью функции генератора send. Чтобы иметь возможность посылать корутине значения, ее надо "запустить", послав в нее None или применив к ней next.

После окончания общения с корутиной ее надо закрыть, при этом в самой корутине можно прописать реакцию на закрытие (с помощью exception, если его не перехватывать, то все равно ничего не произойдет) 

Например, напишем свой grep

In [208]:
def grep_simple(pattern): # also works, but doesn't  Goodbye:(
    print ("Looking for %s" % pattern)
    while True:
        line = (yield)
        if pattern in line:
            print (line)

def grep(pattern):
    print ("Looking for %s" % pattern)
    try:
        while True:
            line = (yield)
            if pattern in line:
                print (line)
    except GeneratorExit:
        print ("Going away. Goodbye")

# Example use
#g = grep_simple("python")
g = grep("python")
g.send(None)


g.send("Yeah, but no, but yeah, but no")
g.send("A series of tubes")
g.send("python generators rock!")
g.close() 

Looking for python
python generators rock!
Going away. Goodbye


Таким образом, меняется наша парадигма - раньше мы сцепляли генераторы друг с другом и последний из них "вытаскивал" данные. Теперь мы можем посылать данные в корутину из другой корутины или основной программы

![coroutines](coroutines.png)

Чтобы не заставлять себя каждый раз посылать "холодному" генератору None, можно написать декоратор

In [211]:
def coroutine(func):
    def start(*args,**kwargs):
        cr = func(*args,**kwargs)
        cr.send(None)
        return cr
    return start

In [212]:
@coroutine
def grep(pattern):
    print ("Looking for %s" % pattern)
    line = ''
    try:
        while True:
            if pattern in line:
                line = (yield line)
            else:
                line = (yield)
    except GeneratorExit:
        print ("Going away. Goodbye")

In [214]:
g = grep("python")

print (g.send("Yeah, but no, but yeah, but no"))
print (g.send("A series of tubes"))
print (g.send("python generators rock!"))
g.close() 

Looking for python
None
None
python generators rock!
Going away. Goodbye


В чем бонусы coroutine? С помощью них можно реализовывать конечные автоматы

![automata](automata.png)

А еще мы можем передавать наши значения сразу в несколько мест! Генераторы в таких случаях бы исчерпались

![coroutines_branching](coroutines_branching.png)

Напишем например, более совершенную версию программы, выдающей все белки

In [398]:
def transcribe(n, tr_table={"A" : "A", "T" : "U", "G" : "G", "C" : "C"}):
    return tr_table[n]

@coroutine
def get_triplets_reader(receiver, ignore_first=0):
    nucleotides = []
    for i in range(ignore_first):
        n = (yield)
        #print ("Triplet reader", ignore_first, n)
        
    while True:
        n = (yield)
        #print ("Triplet reader", ignore_first, n)
        nucleotides.append(n)
        if len(nucleotides) == 3:
            #print ("sending")
            triplet = "".join(nucleotides)
            nucleotides = []
            receiver.send(triplet)
            
@coroutine
def get_proteins_reader(protein_receiver, codons_receiver, name):
    triplets = None
    aminoacids = None
    while True:
        t = (yield)
        
        ac = CODON_TABLE[t]
        #print ("Protein reader", name, t, ac)
        if ac == "M" and triplets is None:
            triplets = [t]
            aminoacids = [ac]
        elif ac == "*" and triplets is not None:
            triplets.append(t)
            protein_receiver.send("".join(aminoacids))
            codons_receiver.send(triplets)
            triplets = None
            aminoacids = None
        elif triplets is not None:
            triplets.append(t)
            aminoacids.append(ac)
            
@coroutine
def get_triplets_counter(cnt):
    while True:
        codons = (yield)
        cnt.update(codons)

@coroutine
def get_proteins_writer(lst):
    while True:
        protein = (yield)
        lst.append(protein)
            

def iter_seqs(in_file_path):
    with open(in_file_path) as in_file:
        in_file.readline()
        letters = chain.from_iterable((line for line in in_file))
        dna_nucleotides = filter(lambda x : x != "\n", letters)
        nucleotides = map(lambda x : transcribe(x.upper()), dna_nucleotides)
       
        codons_cnt = Counter()
        triplets_counter = get_triplets_counter(codons_cnt)
        proteins_lst = []
        proteins_writer = get_proteins_writer(proteins_lst)
        orfs_readers = [get_triplets_reader(get_proteins_reader(proteins_writer,
                                                           triplets_counter, start_pos), 
                                       ignore_first=start_pos)\
                        for start_pos in range(3)]

        for n in nucleotides:
            for reader in orfs_readers:
                reader.send(n)
        
    return proteins_lst, codons_cnt 

In [399]:
path_to_simple_fasta_file = "example.fasta"
with open(path_to_simple_fasta_file, "w") as out_file:
    out_file.write(">example\n")
    out_file.write("ATGTAAATGTAA")

In [404]:
proteins_lst, codons_cnt = iter_seqs(path_to_fasta_file)

In [408]:
codons_cnt

Counter({'AAA': 44178,
         'AAC': 32709,
         'AAG': 23143,
         'AAU': 30160,
         'ACA': 17638,
         'ACC': 33525,
         'ACG': 28215,
         'ACU': 15999,
         'AGA': 14140,
         'AGC': 29603,
         'AGG': 13613,
         'AGU': 16749,
         'AUA': 21081,
         'AUC': 39387,
         'AUG': 76237,
         'AUU': 36398,
         'CAA': 22849,
         'CAC': 21484,
         'CAG': 43663,
         'CAU': 23838,
         'CCA': 24276,
         'CCC': 15446,
         'CCG': 33307,
         'CCU': 14393,
         'CGA': 15273,
         'CGC': 40163,
         'CGG': 23805,
         'CGU': 26240,
         'CUA': 7489,
         'CUC': 17231,
         'CUG': 53366,
         'CUU': 18611,
         'GAA': 39022,
         'GAC': 22113,
         'GAG': 19893,
         'GAU': 35561,
         'GCA': 32215,
         'GCC': 38774,
         'GCG': 46843,
         'GCU': 25462,
         'GGA': 15646,
         'GGC': 36781,
         'GGG': 16321,
         'GG

In [407]:
proteins_lst[0:10]

['MSLCGLKKECLIAASELVTCRE',
 'MKRISTTITTTITITTGNGAG',
 'MQNVFCVLPIFWKAMPGRGRWPPSSLPPPKSPTTWWR',
 'MLYPISAMPNVFLPNF',
 'MSCMALVCWGSARIASTLR',
 'MKKANWWCLDATVPTTLLRCWLPVYAPIVARFGRTLTGSIPATRVRCPMRGC',
 'MKTNYRSRAFPI',
 'MVCAPCVGSRRNSLPHWPAPISTLSPLLRDLLNAQSLSW',
 'MMRPLACALLIRCCSIPIRLSKCL',
 'MYMALIWKTGRKNWRKPKSRLISGA']

Если вам интересно узнать больше о корутинах и Python - отличный сайт http://www.dabeaz.com/tutorials.html.
Про корутины я брал с курса "A Curious Course on Coroutines and Concurrency"

# Subprocess

Иногда нам необходимо вызвать какую-то внешнюю программу и использовать результат ее выполнения

In [51]:
import subprocess

## Просто запустить

Просто запустить программу (почти никогда нам не нужно просто запустить программу, но..)

In [52]:
subprocess.call(["./gen_svg", "out.svg"])

0

Что возвращает нам программа? 

In [55]:
retcod = subprocess.call(["./gen_svg", "out.svg"])

In [58]:
import sys

retcod = subprocess.call(["./gen_svg"])
if retcod != 0:
    print("Error", file=sys.stderr)

Error


## Ругаться на ошибку

In [215]:
subprocess.check_call(["./gen_svg", "out.svg"])

0

In [216]:
subprocess.check_call(["./gen_svg"])

CalledProcessError: Command '['./gen_svg']' returned non-zero exit status 1.

### Shlex

Мы привыкли набирать команду в виде строки - тут же надо с списком мучатся. Можно облегчить себе жизнь

In [74]:
import shlex
cmd = "./gen_svg out.svg"
shlex.split(cmd)

['./gen_svg', 'out.svg']

ВАЖНО использовать именно shlex. Обычный split может обработать некоторые ситуации неверно, например:

In [76]:
import shlex
cmd = "./gen_svg 'out (1).svg'"
print("shlex output:", shlex.split(cmd))
print("python split output:", cmd.split())

shlex output: ['./gen_svg', 'out (1).svg']
python split output: ['./gen_svg', "'out", "(1).svg'"]


In [79]:
cmd = "./gen_svg 'out.svg'"
subprocess.check_call(shlex.split(cmd))

0

## Вывод программы 
Получить вывод программы

In [95]:
cmd = "puzzle --version"
output = subprocess.check_output(shlex.split(cmd))
output

b"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

Что значит b перед строкой?

Python не знает, в какой кодировке будет писать ответ вызываемой программы. Если уверены, что кодировка - utf8, то просто пишите:

In [93]:
output.decode() # same - output.decode(encoding='utf8')

"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

Иначе надо задать decode другую кодировку

## Popen

В целом использовать описанные выше команды из subprocess можно, но обычно этого избегают, а используют более гибкий subprocess.Popen

In [217]:
?subprocess.Popen

Просто запустить процесс

In [98]:
cmd = "./gen_svg out.svg"
process = subprocess.Popen(shlex.split(cmd))
process.wait()

0

Хотим output

In [102]:
cmd = "puzzle --version"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE # указываем, что мы хотим ловить output
                          )
process.wait()
process.stdout.read()

b"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

Так проще:

In [136]:
cmd = "puzzle --version"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE # указываем, что мы хотим ловить stdout
                          )

stdout, _ = process.communicate()
stdout

b"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

А еще можно прямо указать, что мы ожидаем текст, а не бинарный вывод

In [137]:
cmd = "puzzle --version"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           text=True
                          )

stdout, _ = process.communicate()
stdout

"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

In [138]:
cmd = "puzzle --version"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           encoding='utf8',
                           text=True
                          )

stdout, _ = process.communicate()
stdout

"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n"

Хотим ловить информацию из потока ошибок

In [107]:
cmd = "puzzle --version"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.PIPE  # указываем, что мы хотим ловить stderr
                          )

stdout, stderr = process.communicate()
stdout, stderr # оказывается, программа на stderr печатает свою версию в более простом формате
# в stderr могут содержаться важные сообщения типа warning (что не нашлось какого-то файла, потому результат неточен и тд)

(b"\n\n\nWELCOME TO TREE-PUZZLE 5.3.rc16!\n\n\n\nargv[1] = '--version'\n",
 b'puzzle (tree-puzzle) 5.3.rc16\n')

Некоторые программы пишут в stdout и stderr вразнобой - довольно важная информация, которую можно определить только из контекста, бьется на куски не совсем предсказуемым образом. В этом случае можно сказать Popen писать stderr в то же место, что и stdout

In [117]:
cmd = "puzzle --version" 
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT  # перенаправить stderr в stdout
                          )

stdout, _ = process.communicate()
print(stdout.decode())

puzzle (tree-puzzle) 5.3.rc16



WELCOME TO TREE-PUZZLE 5.3.rc16!



argv[1] = '--version'



Можно записывать выдачу программ в отдельный открытый на запись файл

In [122]:
with open("out.log", 'w') as stdout,\
    open("err.log", 'w') as stderr:
    cmd = "puzzle --version"
    process = subprocess.Popen(shlex.split(cmd), 
                           stdout=stdout, # указываем, что мы хотим ловить stdout
                           stderr=stderr  # перенаправить stderr в stdout
                          )

process.communicate()
!cat out.log
!cat err.log




WELCOME TO TREE-PUZZLE 5.3.rc16!



argv[1] = '--version'
puzzle (tree-puzzle) 5.3.rc16


In [124]:
with open("out.log", 'w') as stdout:
    cmd = "puzzle --version"
    process = subprocess.Popen(shlex.split(cmd), 
                           stdout=stdout, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT # перенаправить stderr в stdout
                          )

process.communicate()
!cat out.log

puzzle (tree-puzzle) 5.3.rc16



WELCOME TO TREE-PUZZLE 5.3.rc16!



argv[1] = '--version'


## Как запустить скрипт на Python? 

In [148]:
!cat solution_f.py

import sys

with open(sys.argv[1]) as inp:
    a = inp.readline()
    b = inp.readline()
print(int(a) + int(b))


In [218]:
cmd = "python solution_f.py tests/1.txt"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                           text=True
                          )
print(process.communicate())

('3\n', None)


## Как запустить программу, ожидающую чего-то на stdin

In [146]:
!cat solution.py

a = input()
b = input()
print(int(a) + int(b))


In [219]:
!cat 'tests/1.txt'

1
2


In [220]:
with open('tests/1.txt') as stdin:
    cmd = "python solution.py"
    process = subprocess.Popen(shlex.split(cmd),
                           stdin=stdin, 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                           text=True
                          )
print(process.communicate())

('3\n', None)


## Как запустить программу, которая ожидает строго определенный набор файлов с жестко заданными именами и путями к ним (например, они должны находиться в папке с ней)

На самом деле - таких программ море, тот же PHYLIP для филогении

In [223]:
!cat solution_i.py

import sys

with open("in.txt") as inp:
    a = inp.readline()
    b = inp.readline()
print(int(a) + int(b))


In [224]:
!cat 'tests/1.txt'

1
2


In [ ]:
import os
import shutil


os.mkdir("run")
shutil.copy("solution_i.py", "run/solution_i.py")
shutil.copy("tests/1.txt", "run/in.txt")


In [225]:
!ls run/

in.txt        solution_i.py


In [226]:
cmd = "python solution_i.py"
process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                           text=True,
                           cwd='run' # перед запуском программы система переходит в эту папку. Все пути считаются относительно этой папки 
                          )
print(process.communicate())

('3\n', None)


Как запустить много процессов разом? 

In [232]:
import os
import shutil

In [241]:
procs = []
for i in range(10):
    cmd = "python solution_i.py"
    
    process = subprocess.Popen(shlex.split(cmd), 
                           stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                           stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                           text=True,
                           cwd='run' # перед запуском программы система переходит в эту папку. Все пути считаются относительно этой папки 
                          )
    procs.append(process)

for p in procs:
    print(p.communicate())

('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)
('3\n', None)


Если процессы работают в одной папке и не дай бог пишут одинаковые временные файлы или файлы результатов - то так запустить не получится.
Надо для каждого процесса заводить свою временную папку и в ней работать. 

In [ ]:
import tempfile

In [243]:
procs = []
for i in range(10):
    with tempfile.TemporaryDirectory() as tempdir:
        
        shutil.copy("solution_i.py", os.path.join(tempdir, "solution_i.py"))
        shutil.copy("tests/1.txt", os.path.join(tempdir, "in.txt"))
        cmd = "python solution_i.py"
        p = subprocess.Popen(shlex.split(cmd), 
                               stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                               stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                               text=True,
                               cwd=tempdir # перед запуском программы система переходит в эту папку. Все пути считаются относительно этой папки 
                              )
        p.wait()
    procs.append(p)

for p in procs:
    print(p.stdout.read())

3

3

3

3

3

3

3

3

3

3



При этом потеряли возможность удалять временные папки сразу

Можно сделать вот так

In [257]:
procs = []
for i in range(10):
    tempdir = tempfile.TemporaryDirectory() 
        
    shutil.copy("solution_i.py", os.path.join(tempdir.name, "solution_i.py"))
    shutil.copy("tests/1.txt", os.path.join(tempdir.name, "in.txt"))
    cmd = "python solution_i.py"
    p = subprocess.Popen(shlex.split(cmd), 
                               stdout=subprocess.PIPE, # указываем, что мы хотим ловить stdout
                               stderr=subprocess.STDOUT, # перенаправить stderr в stdout
                               text=True,
                               cwd=tempdir.name# перед запуском программы система переходит в эту папку. Все пути считаются относительно этой папки 
                              )
    procs.append((p, tempdir) )

for p, td in procs:
    p.wait()
    print(p.stdout.read())
    td.cleanup() # удаляем временную папку

3

3

3

3

3

3

3

3

3

3



Но это временное и неудобное решение - with спасал нас от кучи возможных ошибок на случай, если мы забудем закрыть временную папку.
В следующий раз мы разберем модуль **concurrent.futures**, который позволяет все сделать максимально удобно